In [1]:
import json

def read_json_file(file_path: str):
    with open(file_path, 'r') as json_file:
        data = json.load(json_file)
    return data
        
file_path = 'raw_data/2024-09-14_17-31-17.json'
data = read_json_file(file_path)

In [2]:
feature_points_data = {}
for frame in data:
    raw_feature_points = frame.get('rawFeaturePoints')
    if raw_feature_points:
        for identifier, point in zip(raw_feature_points['identifiers'], raw_feature_points['points']):
            feature_points_data.setdefault(identifier, []).append(point)

In [3]:
import numpy as np
from itertools import compress

In [4]:
def filter_points_with_zscore(points, z_scores_threshold = 2.0):
    mean_coordinates = np.mean(points, axis=0)
    std_dev_coordinates = np.std(points, axis=0)
    z_scores = np.abs((points - mean_coordinates) / std_dev_coordinates)
    z_scores = np.nan_to_num(z_scores)
    filtered_points = list(compress(points, np.all(z_scores < z_scores_threshold, axis=1)))
    return filtered_points

In [5]:
feature_points_mean = {}
feature_points_appearing_count = {}
for (identifier, point) in feature_points_data.items():
    filtered_points = filter_points_with_zscore(point)
    feature_points_mean[identifier] = np.mean(filtered_points, axis=0)
    feature_points_appearing_count[identifier] = len(filtered_points)

/var/folders/sk/gjdf8xqs2l7cd33llgw2q7cc0000gn/T/ipykernel_26449/485491658.py:4: RuntimeWarning: invalid value encountered in divide
  z_scores = np.abs((points - mean_coordinates) / std_dev_coordinates)


In [6]:
len(feature_points_data)

27681

In [7]:
import pyvista as pv

max_feature_points_appearing_count = max(feature_points_appearing_count.values())

points = np.array([feature_points_mean[identifier] for identifier in feature_points_mean.keys()])
alphas = np.array([feature_points_appearing_count[identifier] / max_feature_points_appearing_count for identifier in feature_points_appearing_count.keys()])

# Create a PyVista plotter object
plotter = pv.Plotter()

# Create a point cloud with varying transparency
cloud = pv.PolyData(points)
cloud["alpha"] = alphas

# Add the point cloud to the plotter
plotter.add_mesh(cloud, render_points_as_spheres=True, point_size=2, scalars="alpha", opacity="alpha")

# Set labels
plotter.add_axes()
plotter.show_grid(color='black')

# Show plot
plotter.show()

Widget(value='<iframe src="http://localhost:57531/index.html?ui=P_0x15fe149a0_0&reconnect=auto" class="pyvista…

In [8]:
def pipLine(file_path: str):
    data = read_json_file(file_path)
    feature_points_data = {}
    for frame in data:
        raw_feature_points = frame.get('rawFeaturePoints')
        if raw_feature_points:
            for identifier, point in zip(raw_feature_points['identifiers'], raw_feature_points['points']):
                feature_points_data.setdefault(identifier, []).append(point)
    feature_points_mean = {}
    feature_points_appearing_count = {}
    for (identifier, point) in feature_points_data.items():
        filtered_points = filter_points_with_zscore(point)
        feature_points_mean[identifier] = np.mean(filtered_points, axis=0)
        feature_points_appearing_count[identifier] = len(filtered_points)
    max_feature_points_appearing_count = max(feature_points_appearing_count.values())

    feature_points_appearing_conunt_normalized = {}
    for (identifier, count) in feature_points_appearing_count.items():
        feature_points_appearing_conunt_normalized[identifier] = count/max_feature_points_appearing_count
    
    return { 
        "feature_points_mean":feature_points_mean, 
        "feature_points_appearing_conunt_normalized":feature_points_appearing_conunt_normalized 
        }
    

In [9]:
import os
import glob

def get_json_file_name(dirpath):
    json_files = glob.glob(os.path.join(dirpath, '*.json'))
    json_file_names = [os.path.basename(file) for file in json_files]
    return json_file_names

dirpath = 'raw_data'
json_file_names = get_json_file_name(dirpath)
print(json_file_names)

['2024-09-14_17-31-17.json', '2024-09-14_17-40-11.json', '2024-09-14_17-36-03.json']


In [10]:
library= {}
for file_name in json_file_names:
    result = pipLine(f'{dirpath}/{file_name}')
    print(result)
    library[file_name] = result

/var/folders/sk/gjdf8xqs2l7cd33llgw2q7cc0000gn/T/ipykernel_26449/485491658.py:4: RuntimeWarning: invalid value encountered in divide
  z_scores = np.abs((points - mean_coordinates) / std_dev_coordinates)


{'feature_points_mean': {163: array([-4.6021357,  3.4622593, -6.809897 ]), 172: array([-4.385823 ,  3.5592806, -7.04746  ]), 178: array([-2.87150758,  3.0508484 , -4.70734073]), 277: array([-1.0354236,  2.8546367, -6.290929 ]), 304: array([-0.01905141,  0.30495492, -0.39803693]), 685: array([-0.25370306, -0.76845646, -2.12462937]), 721: array([-0.15204617, -0.69187094, -1.9101676 ]), 742: array([-0.11968766, -0.78870027, -2.05426383]), 766: array([-0.07224205, -0.75806208, -2.15164502]), 808: array([ 1.1738036 , -0.57702404, -2.70867698]), 844: array([ 0.86026459, -0.82425629, -2.28852873]), 919: array([ 1.3384795, -0.7753213, -5.522643 ]), 1084: array([ 0.10257047,  0.64998722, -2.48164095]), 1339: array([ 1.11142642, -1.1070629 , -2.32583849]), 1381: array([ 0.63761103,  0.30799049, -3.64733322]), 1411: array([ 0.23316678,  0.6534905 , -2.5405128 ]), 1480: array([-0.22065229, -0.93343338, -1.87289075]), 1603: array([-2.0144701 , -1.50079333, -3.77705666]), 3004: array([ 3.7036836 ,  

In [11]:
class NumpyArrayEncoder(json.JSONEncoder):
    def default(self, obj):
        if isinstance(obj, np.ndarray):
            return obj.tolist()
        return json.JSONEncoder.default(self, obj)
    
json_str = json.dumps(library, cls=NumpyArrayEncoder)

In [12]:
json_str[:100]

'{"2024-09-14_17-31-17.json": {"feature_points_mean": {"163": [-4.602135699999999, 3.4622593, -6.8098'

In [13]:
file_name = "library.json"

# Open the file in write mode
with open(file_name, 'w') as file:
    # Write the string to the file
    file.write(json_str)